In [1]:
import tensorflow as tf
import numpy as np
import sys
sys.path.append('../general')
from pool import Pool
from collections import Counter
from metric import metric

/usr/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
pool = Pool('../data')
model_train_pool, real_test_pool = pool.train_test_split()
train_pool, test_pool = model_train_pool.train_test_split()

In [3]:
class Model:
    def __init__(self, num_features):
        self.POSITIONS = list(range(11))
        self.matrix = tf.get_variable(
            "matrix", shape=(num_features, 1),
            initializer=tf.glorot_uniform_initializer()
        )
        self.bias = tf.get_variable(
            "bias", shape=(1,),
            initializer=tf.glorot_uniform_initializer()
        )
        self.input_features = tf.placeholder('float32', shape=(None, num_features))
        self.input_prediction = tf.placeholder('float32', shape=(None, 1))
        self.output_prediction = tf.matmul(self.input_features, self.matrix) + self.bias
        self.loss = (
            tf.reduce_mean((self.input_prediction - self.output_prediction) ** 2) +
            tf.reduce_mean(self.matrix ** 2) + tf.reduce_mean(self.bias ** 2)
        )
        self.optimizer = tf.train.AdamOptimizer().minimize(
            self.loss, var_list=[self.matrix, self.bias]
        )

        self.sess = tf.Session()
        self.sess.run(tf.global_variables_initializer())
        self.best_marix = self.sess.run(self.matrix)
        self.best_bias = self.sess.run(self.bias)
        
    def teach(self, train_features, train_prediction,
              test_features, test_prediction, verbose=True, iterations=100):
        best_test_loss = 1e111
        for i in range(iterations):
            self.sess.run(
                self.optimizer, {
                    self.input_features: train_features,
                    self.input_prediction: train_prediction
                }
            )
            test_loss = self.get_regression_loss(test_features, test_prediction)
            train_loss = self.get_regression_loss(train_features, train_prediction)
            test_loss = test_loss[0]
            train_loss = train_loss[0]
            if test_loss < best_test_loss:
                self.best_marix = self.sess.run(self.matrix)
                self.best_bias = self.sess.run(self.bias)
                best_test_loss = test_loss
            if verbose:
                real_loss = self.get_regression_loss(
                    real_test_pool.regression_features,
                    real_test_pool.regression_prediction
                )
                print(
                    "train loss: {}, test loss: {}, real_test: {}".format(
                        train_loss, test_loss, real_loss
                    )
                )

    def predict_score(self, features):
        return self.sess.run(self.output_prediction, {self.input_features: features})

    def get_regression_loss(self, features, prediction):
         return self.sess.run(
            self.loss, {
                self.input_features: features,
                self.input_prediction: prediction
            }
        ),

    def predict_positions(self, test_features):
        prediction = []
        for features in test_features:
            max_score = -100
            best_position = -100
            for position in self.POSITIONS:
                new_score = self.predict_score([
                    list(features) + [
                        0 if possible_position != position else 1
                        for possible_position in self.POSITIONS
                    ]
                ])
                new_score = new_score[0]
                print(new_score)
                if new_score > max_score:
                    max_score = new_score
                    best_position = position
            prediction.append(best_position)
        return prediction

In [ ]:
model = Model(len(pool.regression_features[0]))
model.teach(
    train_pool.regression_features, train_pool.regression_prediction,
    test_pool.regression_features, test_pool.regression_prediction
)

train loss: 22.3662109375, test loss: 21.096410751342773, real_test: (142.37059,)
train loss: 20.810733795166016, test loss: 19.60530662536621, real_test: (157.62978,)
train loss: 19.511486053466797, test loss: 18.369583129882812, real_test: (174.24126,)
train loss: 18.410842895507812, test loss: 17.332021713256836, real_test: (192.14763,)
train loss: 17.454910278320312, test loss: 16.438251495361328, real_test: (211.29297,)
train loss: 16.60272216796875, test loss: 15.647296905517578, real_test: (231.63373,)
train loss: 15.82729434967041, test loss: 14.932503700256348, real_test: (253.14005,)
train loss: 15.11259651184082, test loss: 14.278107643127441, real_test: (275.79343,)
train loss: 14.449320793151855, test loss: 13.675078392028809, real_test: (299.58087,)
train loss: 13.831689834594727, test loss: 13.117772102355957, real_test: (324.49316,)
train loss: 13.255868911743164, test loss: 12.60220718383789, real_test: (350.5211,)
train loss: 12.719303131103516, test loss: 12.12531852

train loss: 2.458181381225586, test loss: 2.5002100467681885, real_test: (5809.494,)
train loss: 2.439089775085449, test loss: 2.4807324409484863, real_test: (5897.8022,)
train loss: 2.4203784465789795, test loss: 2.4616594314575195, real_test: (5986.4756,)


In [ ]:
position_predictions = model.predict_positions(test_pool.features)
metric(position_predictions, test_pool.positions, test_pool.targets, test_pool.probas)

[1.9825106]
[2.003511]
[2.108603]
[2.0168853]
[2.102847]
[2.0600896]
[2.0364032]
[2.0903618]
[2.0306294]
[2.0177705]
[2.1272907]
[-0.20774996]
[-0.18674934]
[-0.08165753]
[-0.17337525]
[-0.08741343]
[-0.1301707]
[-0.15385711]
[-0.0998987]
[-0.15963113]
[-0.17248976]
[-0.06296933]
[0.39000458]
[0.41100526]
[0.516097]
[0.42437935]
[0.51034135]
[0.46758407]
[0.44389766]
[0.49785608]
[0.43812352]
[0.4252649]
[0.53478533]
[-0.34616697]
[-0.32516634]
[-0.22007453]
[-0.31179225]
[-0.2258302]
[-0.26858747]
[-0.29227412]
[-0.23831546]
[-0.2980479]
[-0.31090677]
[-0.20138633]
[0.42736518]
[0.4483657]
[0.55345756]
[0.4617399]
[0.54770184]
[0.50494456]
[0.48125803]
[0.53521657]
[0.47548413]
[0.46262538]
[0.5721458]
[0.70101637]
[0.722017]
[0.82710874]
[0.73539114]
[0.8213531]
[0.7785957]
[0.75490916]
[0.8088677]
[0.7491354]
[0.7362765]
[0.84579694]
[0.14336365]
[0.16436428]
[0.2694561]
[0.17773831]
[0.2637002]
[0.22094291]
[0.1972565]
[0.25121492]
[0.19148248]
[0.17862386]
[0.28814405]
[-1.2135724

[1.1259573]
[1.2354777]
[0.08658373]
[0.10758436]
[0.21267617]
[0.12095845]
[0.20692039]
[0.16416311]
[0.14047664]
[0.19443536]
[0.13470286]
[0.12184399]
[0.23136449]
[0.40460908]
[0.4256097]
[0.5307015]
[0.43898386]
[0.52494586]
[0.48218858]
[0.45850205]
[0.5124606]
[0.45272815]
[0.43986928]
[0.54938984]
[0.05111361]
[0.07211423]
[0.17720604]
[0.08548844]
[0.17145026]
[0.12869298]
[0.10500658]
[0.15896499]
[0.09923255]
[0.08637393]
[0.1958943]
[0.36820996]
[0.38921058]
[0.49430227]
[0.4025846]
[0.4885466]
[0.44578922]
[0.4221028]
[0.47606122]
[0.4163288]
[0.40347004]
[0.5129906]
[0.9974437]
[1.0184443]
[1.1235361]
[1.0318185]
[1.1177804]
[1.0750232]
[1.0513365]
[1.1052951]
[1.0455627]
[1.0327039]
[1.1422243]
[0.3572756]
[0.37827623]
[0.48336804]
[0.39165038]
[0.47761238]
[0.4348551]
[0.41116858]
[0.465127]
[0.40539467]
[0.39253592]
[0.50205636]
[0.41071934]
[0.43172002]
[0.53681177]
[0.4450941]
[0.53105617]
[0.48829865]
[0.46461225]
[0.51857066]
[0.45883846]
[0.4459796]
[0.55550003]
[

[1.3860496]
[1.3432924]
[1.3196057]
[1.3735644]
[1.3138319]
[1.3009729]
[1.4104935]
[1.4163268]
[1.4373274]
[1.5424193]
[1.4507016]
[1.5366635]
[1.4939063]
[1.4702199]
[1.5241783]
[1.4644458]
[1.451587]
[1.5611074]
[0.39479494]
[0.41579556]
[0.5208875]
[0.4291697]
[0.5151316]
[0.47237456]
[0.4486879]
[0.50264657]
[0.4429139]
[0.43005526]
[0.53957546]
[0.8974812]
[0.9184817]
[1.0235735]
[0.93185586]
[1.017818]
[0.9750607]
[0.9513742]
[1.0053326]
[0.94560015]
[0.9327415]
[1.0422618]
[-0.3190949]
[-0.29809427]
[-0.19300246]
[-0.28472018]
[-0.19875813]
[-0.2415154]
[-0.26520193]
[-0.21124339]
[-0.27097583]
[-0.2838347]
[-0.17431426]
[0.4542336]
[0.4752342]
[0.580326]
[0.48860836]
[0.57457036]
[0.5318131]
[0.50812656]
[0.562085]
[0.50235265]
[0.4894938]
[0.5990142]
[-0.22864687]
[-0.20764625]
[-0.10255444]
[-0.19427216]
[-0.10830998]
[-0.15106738]
[-0.1747539]
[-0.12079537]
[-0.1805278]
[-0.19338655]
[-0.08386624]
[0.64698476]
[0.66798526]
[0.7730772]
[0.6813595]
[0.76732165]
[0.72456414]
[

[0.9305661]
[0.40080494]
[0.42180556]
[0.52689743]
[0.4351797]
[0.5211416]
[0.47838432]
[0.4546979]
[0.5086563]
[0.4489239]
[0.43606502]
[0.5455857]
[-0.16428995]
[-0.14328921]
[-0.0381974]
[-0.129915]
[-0.04395294]
[-0.08671045]
[-0.11039686]
[-0.05643845]
[-0.11617088]
[-0.12902975]
[-0.01950932]
[0.56989616]
[0.5908967]
[0.69598854]
[0.60427094]
[0.69023275]
[0.6474755]
[0.6237891]
[0.6777476]
[0.61801517]
[0.6051563]
[0.71467686]
[0.27138793]
[0.29238856]
[0.39748013]
[0.3057626]
[0.3917247]
[0.3489672]
[0.3252808]
[0.3792392]
[0.319507]
[0.30664814]
[0.41616857]
[-1.4326609]
[-1.4116601]
[-1.3065683]
[-1.398286]
[-1.3123244]
[-1.3550814]
[-1.3787678]
[-1.3248094]
[-1.3845419]
[-1.3974007]
[-1.2878803]
[0.25294173]
[0.27394235]
[0.3790341]
[0.28731644]
[0.37327856]
[0.33052105]
[0.30683464]
[0.36079305]
[0.30106086]
[0.288202]
[0.39772242]
[0.4902768]
[0.51127756]
[0.61636937]
[0.52465165]
[0.6106136]
[0.5678563]
[0.5441698]
[0.5981283]
[0.5383959]
[0.52553713]
[0.63505757]
[1.3906

[0.6890199]
[0.7941117]
[0.70239407]
[0.78835607]
[0.7455987]
[0.7219122]
[0.7758707]
[0.7161383]
[0.7032795]
[0.81279993]
[0.4822814]
[0.503282]
[0.6083738]
[0.51665616]
[0.6026181]
[0.55986077]
[0.53617436]
[0.5901328]
[0.53040045]
[0.5175416]
[0.6270621]
[0.15106732]
[0.17206794]
[0.27715975]
[0.18544209]
[0.27140397]
[0.2286467]
[0.20496029]
[0.2589187]
[0.19918627]
[0.18632764]
[0.29584807]
[0.44231665]
[0.46331728]
[0.5684091]
[0.47669148]
[0.5626534]
[0.51989615]
[0.49620962]
[0.55016816]
[0.49043572]
[0.47757685]
[0.5870974]
[0.61833984]
[0.63934046]
[0.7444323]
[0.6527146]
[0.7386766]
[0.69591933]
[0.6722328]
[0.7261912]
[0.6664588]
[0.65360016]
[0.7631205]
[1.660752]
[1.6817527]
[1.7868445]
[1.6951268]
[1.7810887]
[1.7383314]
[1.7146449]
[1.7686034]
[1.7088711]
[1.6960123]
[1.8055326]
[1.4253452]
[1.4463458]
[1.5514376]
[1.4597199]
[1.545682]
[1.5029247]
[1.4792382]
[1.5331966]
[1.4734641]
[1.4606055]
[1.5701258]
[0.2545669]
[0.27556753]
[0.38065946]
[0.28894168]
[0.3749038]


...

[0.17173332]
[0.11200088]
[0.09914196]
[0.20866245]
[0.2636751]
[0.28467578]
[0.38976753]
[0.2980498]
[0.38401192]
[0.34125453]
[0.31756812]
[0.37152654]
[0.3117941]
[0.29893535]
[0.4084558]
[0.6198392]
[0.6408398]
[0.7459316]
[0.6542139]
[0.7401759]
[0.69741863]
[0.6737321]
[0.72769064]
[0.6679582]
[0.65509933]
[0.76461977]
[0.42062742]
[0.44162804]
[0.54671997]
[0.4550022]
[0.5409642]
[0.4982069]
[0.47452027]
[0.5284788]
[0.46874636]
[0.45588762]
[0.56540805]
[-0.8881961]
[-0.8671955]
[-0.7621037]
[-0.8538213]
[-0.76785934]
[-0.8106166]
[-0.834303]
[-0.7803446]
[-0.84007704]
[-0.8529357]
[-0.7434155]
[0.82254255]
[0.8435432]
[0.9486351]
[0.8569175]
[0.9428793]
[0.90012205]
[0.87643564]
[0.93039405]
[0.8706616]
[0.85780275]
[0.9673234]
[0.71808076]
[0.7390814]
[0.8441732]
[0.7524556]
[0.83841753]
[0.79566014]
[0.7719736]
[0.82593215]
[0.7661997]
[0.75334096]
[0.8628614]
[1.489217]
[1.5102177]
[1.6153095]
[1.5235919]
[1.6095537]
[1.5667964]
[1.5431098]
[1.5970684]
[1.537336]
[1.5244771

[0.01095247]
[1.7718033]
[1.7928038]
[1.8978956]
[1.8061779]
[1.89214]
[1.8493828]
[1.8256961]
[1.8796548]
[1.8199223]
[1.8070635]
[1.9165839]
[1.0270019]
[1.0480025]
[1.1530944]
[1.0613766]
[1.1473386]
[1.1045812]
[1.0808947]
[1.1348532]
[1.0751208]
[1.062262]
[1.1717825]
[0.94364727]
[0.9646479]
[1.0697395]
[0.97802186]
[1.063984]
[1.0212265]
[0.9975401]
[1.0514988]
[0.9917661]
[0.97890747]
[1.0884279]
[0.06336093]
[0.08436155]
[0.18945342]
[0.09773564]
[0.18369776]
[0.14094025]
[0.11725384]
[0.17121226]
[0.11148006]
[0.09862113]
[0.20814162]
[0.3049494]
[0.3259499]
[0.43104178]
[0.33932412]
[0.42528617]
[0.3825289]
[0.3588425]
[0.4128009]
[0.35306847]
[0.34020984]
[0.44973004]
[0.97448045]
[0.9954811]
[1.1005728]
[1.0088552]
[1.0948172]
[1.0520599]
[1.0283735]
[1.0823319]
[1.0225995]
[1.0097408]
[1.119261]
[1.2275617]
[1.2485625]
[1.3536541]
[1.2619365]
[1.3478985]
[1.3051411]
[1.2814547]
[1.3354132]
[1.2756808]
[1.2628219]
[1.3723425]
[-0.21191168]
[-0.19091105]
[-0.08581924]
[-0.1

[0.3948992]
[0.4158998]
[0.5209916]
[0.42927396]
[0.51523584]
[0.47247857]
[0.44879216]
[0.5027506]
[0.44301814]
[0.4301595]
[0.5396798]
[3.0073638]
[3.0283642]
[3.1334562]
[3.0417385]
[3.1277008]
[3.0849433]
[3.061257]
[3.1152153]
[3.0554829]
[3.0426245]
[3.152145]
[0.39552838]
[0.416529]
[0.52162075]
[0.4299031]
[0.5158651]
[0.4731078]
[0.4494213]
[0.5033798]
[0.44364738]
[0.43078852]
[0.5403091]
[1.0444609]
[1.0654616]
[1.1705536]
[1.0788357]
[1.1647977]
[1.1220404]
[1.0983537]
[1.1523124]
[1.09258]
[1.0797213]
[1.1892418]
[1.3980762]
[1.4190768]
[1.5241686]
[1.432451]
[1.518413]
[1.4756557]
[1.4519691]
[1.5059276]
[1.4461952]
[1.4333364]
[1.5428569]
[-0.17568254]
[-0.15468192]
[-0.04958999]
[-0.14130759]
[-0.05534577]
[-0.09810305]
[-0.12178946]
[-0.06783104]
[-0.12756348]
[-0.14042234]
[-0.03090191]
[0.64535743]
[0.66635805]
[0.77144986]
[0.6797322]
[0.7656942]
[0.7229368]
[0.6992504]
[0.7532088]
[0.6934765]
[0.68061775]
[0.79013807]
[0.8275533]
[0.8485539]
[0.9536458]
[0.86192805

[1.212621]
[1.1889341]
[1.2428925]
[1.1831603]
[1.1703014]
[1.2798221]
[-0.398129]
[-0.37712836]
[-0.27203655]
[-0.36375415]
[-0.27779222]
[-0.3205496]
[-0.34423614]
[-0.2902776]
[-0.35000992]
[-0.3628688]
[-0.25334835]
[-0.81413114]
[-0.7931305]
[-0.6880387]
[-0.7797564]
[-0.69379437]
[-0.7365519]
[-0.7602383]
[-0.7062799]
[-0.7660123]
[-0.7788712]
[-0.66935074]
[2.0618043]
[2.082805]
[2.1878967]
[2.096179]
[2.182141]
[2.1393838]
[2.1156974]
[2.1696558]
[2.1099234]
[2.0970645]
[2.206585]
[1.2034365]
[1.2244371]
[1.329529]
[1.2378112]
[1.3237734]
[1.2810159]
[1.2573295]
[1.3112879]
[1.2515554]
[1.2386966]
[1.348217]
[0.91023374]
[0.9312344]
[1.0363262]
[0.94460857]
[1.0305704]
[0.9878131]
[0.9641267]
[1.0180851]
[0.9583527]
[0.94549406]
[1.0550145]
[0.809256]
[0.83025664]
[0.93534845]
[0.8436308]
[0.9295928]
[0.8868355]
[0.863149]
[0.9171075]
[0.8573751]
[0.8445162]
[0.95403665]
[0.46013993]
[0.4811406]
[0.58623236]
[0.4945147]
[0.5804767]
[0.5377194]
[0.5140328]
[0.5679913]
[0.508259]

[1.9027042]
[1.8109865]
[1.8969486]
[1.8541911]
[1.8305047]
[1.8844631]
[1.8247309]
[1.811872]
[1.9213924]
[1.1326239]
[1.1536245]
[1.2587163]
[1.1669986]
[1.2529608]
[1.2102033]
[1.1865169]
[1.2404753]
[1.1807431]
[1.1678842]
[1.2774047]
[0.69484234]
[0.71584296]
[0.8209348]
[0.72921705]
[0.81517905]
[0.7724218]
[0.74873525]
[0.80269367]
[0.74296135]
[0.7301026]
[0.8396229]
[1.3197981]
[1.3407989]
[1.4458905]
[1.354173]
[1.4401349]
[1.3973776]
[1.3736911]
[1.4276496]
[1.3679173]
[1.3550584]
[1.4645787]
[1.1594621]
[1.1804627]
[1.2855545]
[1.1938369]
[1.2797989]
[1.2370415]
[1.2133551]
[1.2673135]
[1.2075813]
[1.1947224]
[1.3042428]
[0.17629611]
[0.19729668]
[0.3023885]
[0.21067083]
[0.29663277]
[0.2538755]
[0.23018897]
[0.2841475]
[0.22441506]
[0.21155632]
[0.32107675]
[0.19199258]
[0.2129932]
[0.318085]
[0.22636735]
[0.31232935]
[0.26957208]
[0.24588567]
[0.2998441]
[0.24011165]
[0.22725302]
[0.33677334]
[0.9973974]
[1.018398]
[1.1234899]
[1.0317721]
[1.1177342]
[1.0749768]
[1.051290

In [ ]:
score_prediction = model.predict_score(real_test_pool.regression_features)
np.mean((score_prediction - real_test_pool.targets) ** 2)

In [ ]:
Counter(position_predictions)